In [4]:
import pandas as pd
import numpy as np
import string
string .punctuation
data = pd.read_csv(r'c:\Users\shiya\OneDrive\Desktop\textsummarizer\Reduced_Dataset.csv')
data_headline =data[['headline']]
data=data[['text']]


In [1]:
import string
def remove_punctuation_and_convert_to_lowercase(text):
    if isinstance(text, str):
        # Remove all punctuation and convert to lowercase
        translator = str.maketrans('', '', string.punctuation)
        cleaned_text = text.translate(translator).lower()
        return cleaned_text
    else:
        return str(text)


if 'text' in data.columns:
    data['text'] = data['text'].replace(np.nan,'',regex=True)
    data['cleaned_text'] = data['text'].apply(remove_punctuation_and_convert_to_lowercase)




NameError: name 'data' is not defined

In [6]:
import nltk
from nltk.tokenize import word_tokenize, sent_tokenize

def tokenize_text(text):
    # Tokenize the text into sentences.
    sentences = sent_tokenize(text)

    # Tokenize each sentence into words.
    tokenized_text = []
    for sentence in sentences:
        words = word_tokenize(sentence)
        tokenized_text.append(words)

    return tokenized_text

if 'cleaned_text' in data.columns:
    data['tokenized_text'] = data['cleaned_text'].apply(tokenize_text)

print(data['tokenized_text'])


0       [[if, youre, a, photographer, keep, all, the, ...
1       [[see, the, image, for, how, this, drawing, de...
2       [[it, is, possible, to, become, a, vfx, artist...
3       [[the, best, art, investors, do, their, resear...
4       [[as, you, start, planning, for, a, project, o...
                              ...                        
9775    [[if, you, want, to, make, your, fantasy, worl...
9776    [[in, a, perzine, a, predominantly, personal, ...
9777    [[decide, on, a, newspaper, that, is, most, ap...
9778    [[write, down, all, of, the, positive, feature...
9779    [[as, fantasy, stories, can, include, a, lot, ...
Name: tokenized_text, Length: 9780, dtype: object


In [7]:
import nltk
from nltk.corpus import stopwords

def remove_stopwords(list_of_lists):
    stopwords = set(nltk.corpus.stopwords.words('english'))
    filtered_list_of_lists = []
    for list_of_strings in list_of_lists:
        filtered_list_of_strings = []
        for string in list_of_strings:
            if string not in stopwords:
                filtered_list_of_strings.append(string)
        filtered_list_of_lists.append(filtered_list_of_strings)
    return filtered_list_of_lists





In [8]:
data['text'] = data['tokenized_text'].apply(remove_stopwords)

print(data['text'])

0       [[youre, photographer, keep, necessary, lens, ...
1       [[see, image, drawing, develops, stepbystep, ....
2       [[possible, become, vfx, artist, without, coll...
3       [[best, art, investors, research, pieces, art,...
4       [[start, planning, project, work, youll, likel...
                              ...                        
9775    [[want, make, fantasy, world, feel, real, incl...
9776    [[perzine, predominantly, personal, zine, zine...
9777    [[decide, newspaper, appropriate, purposes, au...
9778    [[write, positive, features, associated, produ...
9779    [[fantasy, stories, include, lot, twists, turn...
Name: text, Length: 9780, dtype: object


In [9]:
from nltk.stem import WordNetLemmatizer
nltk.download('omw-1.4')
nltk.download('wordnet')

wordnet_lemmatizer = WordNetLemmatizer()
def lemmatize_list_of_lists(list_of_lists):
  

  lemmatized_list_of_lists = []
  for list_of_strings in list_of_lists:
    lemmatized_list_of_strings = []
    for string in list_of_strings:
      lemmatized_string = wordnet_lemmatizer.lemmatize(string)
      lemmatized_list_of_strings.append(lemmatized_string)
    lemmatized_list_of_lists.append(lemmatized_list_of_strings)
  return lemmatized_list_of_lists



[nltk_data] Downloading package omw-1.4 to
[nltk_data]     C:\Users\shiya\AppData\Roaming\nltk_data...
[nltk_data]   Package omw-1.4 is already up-to-date!
[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\shiya\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


In [10]:
data['text'] = data['text'].apply(lemmatize_list_of_lists)

print(data['text'])

0       [[youre, photographer, keep, necessary, lens, ...
1       [[see, image, drawing, develops, stepbystep, ....
2       [[possible, become, vfx, artist, without, coll...
3       [[best, art, investor, research, piece, art, b...
4       [[start, planning, project, work, youll, likel...
                              ...                        
9775    [[want, make, fantasy, world, feel, real, incl...
9776    [[perzine, predominantly, personal, zine, zine...
9777    [[decide, newspaper, appropriate, purpose, aud...
9778    [[write, positive, feature, associated, produc...
9779    [[fantasy, story, include, lot, twist, turn, o...
Name: text, Length: 9780, dtype: object


In [25]:
from sklearn.feature_extraction.text import CountVectorizer
import networkx as nx

all_summaries = []

def summarize_text(article_text):
    article_text = ' '.join(article_text)

    if not article_text or len(article_text.split()) < 3:
        return [] 

    vectorizer = CountVectorizer()
    X = vectorizer.fit_transform([article_text])
    co_occurrence_matrix = (X.T * X)

    G = nx.Graph(co_occurrence_matrix)
    textrank_scores = nx.pagerank(G, alpha=0.85)

    num_top_sentences = 6 

    sentences = article_text.split('.')
    sorted_sentences = sorted(sentences, key=lambda sentence: textrank_scores.get(sentence, 0), reverse=True)
    summary = sorted_sentences[:num_top_sentences]

    return summary


In [ ]:
for article_text in data['text']:
    if not isinstance(article_text, list):
        continue
    article_text = [', '.join(sublist) for sublist in article_text]
    summary = summarize_text(article_text)
    all_summaries.append(summary)


In [26]:
print(all_summaries)

[['youre, photographer, keep, necessary, lens, cord, battery, quadrant, home, studio, ', ' paint, kept, brush, cleaner, canvas, print, supply, ink, etc, ', ' make, broader, group, area, supply, make, finding, easier, limiting, search, much, smaller, area, ', ' idea, include, essential, supply, area, thing, use, every, day, ', ' inspiration, reference, area, ', ' dedicated, work, area, '], ['see, image, drawing, develops, stepbystep, ', ' however, important, detail, following, drawing, examine, create, something, unique, ', ' use, line, create, image, shape, section, ', ' fill, appeared, section, different, pattern, ornament, ', ' add, text, needed, example, neopoprealism, 25, add, colored, strip, top, color, wish, ', ' painting, mural, always, requires, preparation, '], ['possible, become, vfx, artist, without, college, degree, path, often, easier, one, ', ' vfx, artist, usually, major, fine, art, computer, graphic, animation, ', ' choose, college, reputation, strength, area, reputatio

In [29]:
def remove_commas_from_list(input_list):
    modified_list = []

    for item in input_list:
        words = item.split(',')
        sentence = ' '.join(words)
        modified_list.append(sentence)

    return modified_list
data_output=[]
for input_list in all_summaries:
    modified_list = remove_commas_from_list(input_list)
    result = ' '.join(modified_list)
    data_output.append([result])
    



In [30]:
print(data_output)

[['youre  photographer  keep  necessary  lens  cord  battery  quadrant  home  studio    paint  kept  brush  cleaner  canvas  print  supply  ink  etc    make  broader  group  area  supply  make  finding  easier  limiting  search  much  smaller  area    idea  include  essential  supply  area  thing  use  every  day    inspiration  reference  area    dedicated  work  area  '], ['see  image  drawing  develops  stepbystep    however  important  detail  following  drawing  examine  create  something  unique    use  line  create  image  shape  section    fill  appeared  section  different  pattern  ornament    add  text  needed  example  neopoprealism  25  add  colored  strip  top  color  wish    painting  mural  always  requires  preparation  '], ['possible  become  vfx  artist  without  college  degree  path  often  easier  one    vfx  artist  usually  major  fine  art  computer  graphic  animation    choose  college  reputation  strength  area  reputation  good  job  placement  graduate   

In [31]:
print(len(data_output))

9780
